In [0]:
# List all files in the gold layer to verify

dbutils.fs.ls("/mnt/gold")

[]

In [0]:
# Define the path to the Retail_Dataset.parquet in the Silver container
silver_path = "dbfs:/mnt/silver/Retail_Dataset.parquet"

# Read the Parquet file from the Silver container into a DataFrame
silver_df = spark.read.parquet(silver_path)

# Display the DataFrame (optional, for verification)
display(silver_df)


sale_id quantity_sold unit_price payment_method discount_applied total_price sale_date customer_name gender loyalty_points age email phone_number address city state country product_name product_id category brand cost_price selling_price supplier_id store_name store_id location manager_name opening_date store_type inventory_id stock_quantity last_restock_date supplier_name 2 2 101.83000183105469 Credit Card 15.329999923706055 203.66000366210938 2024-11-09 Danielle Castro Male 1150 57 warebrittany@gmail.com 6836459326 614 Robles Square Erinside MN Carlaview Connecticut Sudan Who 43 Clothing Mcconnell, Braun and Newman 137.24 18.22 8 Butler LLC 32 Lake Kyle Gregory Ayala 2020-02-23 Clothing 676 438 2024-08-16 Garcia, Walker and Hancock 2 2 101.83000183105469 Credit Card 15.329999923706055 203.66000366210938 2024-11-09 Danielle Castro Male 1150 57 warebrittany@gmail.com 6836459326 614 Robles Square Erinside MN Carlaview Connecticut Sudan Who 43 Clothing Mcconnell, Braun and Newman 137.24 18.22 8 Butler LLC 32 Lake Kyle Gregory Ayala 2020-02-23 Clothing 496 236 2025-02-22 Gonzalez, Huerta and Harding 3 9 131.7899932861328 Debit Card 9.4399995803833 1186.1099853515625 2025-01-27 James Moore Male 1628 33 stanley37@hotmail.com 001-603-689-010207922 597 Thomas Trail North Brenda New Antonioberg Maine Egypt Hold 437 Clothing Mcdaniel, Mahoney and Weaver 8.66 240.74 35 Jones Inc 28 East Steven Jane Beard 2023-05-09 Electronics 786 433 2024-10-03 Smith-Mack 3 9 131.7899932861328 Debit Card 9.4399995803833 1186.1099853515625 2025-01-27 James Moore Male 1628 33 stanley37@hotmail.com 001-603-689-010207922 597 Thomas Trail North Brenda New Antonioberg Maine Egypt Hold 437 Clothing Mcdaniel, Mahoney and Weaver 8.66 240.74 35 Jones Inc 28 East Steven Jane Beard 2023-05-09 Electronics 777 87 2024-05-19 Fox-Vega 3 9 131.7899932861328 Debit Card 9.4399995803833 1186.1099853515625 2025-01-27 James Moore Male 1628 33 stanley37@hotmail.com 001-603-689-010207922 597 Thomas Trail North Brenda New Antonioberg Maine Egypt Hold 437 Clothing Mcdaniel, Mahoney and Weaver 8.66 240.74 35 Jones Inc 28 East Steven Jane Beard 2023-05-09 Electronics 568 465 2024-09-23 Logan, Ponce and Clark 3 9 131.7899932861328 Debit Card 9.4399995803833 1186.1099853515625 2025-01-27 James Moore Male 1628 33 stanley37@hotmail.com 001-603-689-010207922 597 Thomas Trail North Brenda New Antonioberg Maine Egypt Hold 437 Clothing Mcdaniel, Mahoney and Weaver 8.66 240.74 35 Jones Inc 28 East Steven Jane Beard 2023-05-09 Electronics 539 329 2024-12-01 Hendricks, Brown and Martinez 3 9 131.7899932861328 Debit Card 9.4399995803833 1186.1099853515625 2025-01-27 James Moore Male 1628 33 stanley37@hotmail.com 001-603-689-010207922 597 Thomas Trail North Brenda New Antonioberg Maine Egypt Hold 437 Clothing Mcdaniel, Mahoney and Weaver 8.66 240.74 35 Jones Inc 28 East Steven Jane Beard 2023-05-09 Electronics 274 18 2024-09-24 Newman-Gonzalez 5 9 143.24000549316406 Cash 13.699999809265137 1289.1600341796875 2024-08-12 Joshua Harris Male 2748 64 josephbrooks@yahoo.com 365.540.3984 2317 Katherine Pass Apt. 492 Smithbury Wisconsin Somalia Contain 176 Toys Singleton LLC 38.41 90.89 44 Shaw, Lane and Hess 4 Wangton Jimmy Smith 2020-07-21 Grocery 810 334 2025-02-13 Cox PLC 5 9 143.24000549316406 Cash 13.699999809265137 1289.1600341796875 2024-08-12 Joshua Harris Male 2748 64 josephbrooks@yahoo.com 365.540.3984 2317 Katherine Pass Apt. 492 Smithbury Wisconsin Somalia Contain 176 Toys Singleton LLC 38.41 90.89 44 Shaw, Lane and Hess 4 Wangton Jimmy Smith 2020-07-21 Grocery 780 471 2024-08-27 Huffman LLC 5 9 143.24000549316406 Cash 13.699999809265137 1289.1600341796875 2024-08-12 Joshua Harris Male 2748 64 josephbrooks@yahoo.com 365.540.3984 2317 Katherine Pass Apt. 492 Smithbury Wisconsin Somalia Contain 176 Toys Singleton LLC 38.41 90.89 44 Shaw, Lane and Hess 4 Wangton Jimmy Smith 2020-07-21 Grocery 631 309 2025-01-04 Orr, Glenn and Duncan 5 9 143.24000549316406 Cash 13.699999809265137 1289.1600341

In [0]:
%python
# Define facts (numerical measures)
facts_df = silver_df.select(
    "sale_id", "quantity_sold", "unit_price", "total_price", 
    "discount_applied", "payment_method", "sale_date"
)

# Define dimensions (categorical attributes)
customer_dim_df = silver_df.select(
    "customer_name", "gender", "loyalty_points", "email", 
    "phone_number", "address", "city", "state", "country"
)

product_dim_df = silver_df.select(
    "product_id", "product_name", "category", "brand", "cost_price", "selling_price"
)

store_dim_df = silver_df.select(
    "store_id", "store_name", "location", "manager_name", "opening_date", "store_type"
)

inventory_dim_df = silver_df.select(
    "inventory_id", "stock_quantity", "last_restock_date", "supplier_name"
)

# Function to remove all files in a folder (if any exist)
def remove_existing_files(folder_path):
    # List files in the folder
    files = dbutils.fs.ls(folder_path)
    
    # Remove all files in the folder
    for file in files:
        dbutils.fs.rm(file.path, True)
        print(f"Removed {file.name}")

# Define the path for the Gold container
gold_folder = "dbfs:/mnt/gold/"

# First, remove all existing files in the Gold container
remove_existing_files(gold_folder)

# Write the Facts to the Gold container
facts_df.write.mode("overwrite").parquet(gold_folder + "fact_table.parquet")

# Write the Dimensions to the Gold container
customer_dim_df.write.mode("overwrite").parquet(gold_folder + "dim_customer.parquet")
product_dim_df.write.mode("overwrite").parquet(gold_folder + "dim_product.parquet")
store_dim_df.write.mode("overwrite").parquet(gold_folder + "dim_store.parquet")
inventory_dim_df.write.mode("overwrite").parquet(gold_folder + "dim_inventory.parquet")

# Verify the files are written in the Gold container
dbutils.fs.ls(gold_folder)



Removed dim_customer.parquet/
Removed dim_inventory.parquet/
Removed dim_product.parquet/
Removed dim_store.parquet/
Removed fact_table.parquet/


[FileInfo(path='dbfs:/mnt/gold/dim_customer.parquet/', name='dim_customer.parquet/', size=0, modificationTime=1745835436000),
 FileInfo(path='dbfs:/mnt/gold/dim_inventory.parquet/', name='dim_inventory.parquet/', size=0, modificationTime=1745835437000),
 FileInfo(path='dbfs:/mnt/gold/dim_product.parquet/', name='dim_product.parquet/', size=0, modificationTime=1745835436000),
 FileInfo(path='dbfs:/mnt/gold/dim_store.parquet/', name='dim_store.parquet/', size=0, modificationTime=1745835437000),
 FileInfo(path='dbfs:/mnt/gold/fact_table.parquet/', name='fact_table.parquet/', size=0, modificationTime=1745835435000)]

In [0]:
%python
# Function to remove unwanted files and rename the final part file
def remove_and_rename_files(folder_path, new_name):
    # List files in the folder
    files = dbutils.fs.ls(folder_path)
    
    # Remove _SUCCESS, _committed, _started, and part files
    for file in files:
        if file.name.startswith(('_SUCCESS', '_committed', '_started')):
            dbutils.fs.rm(file.path, True)
            print(f"Removed {file.name}")
    
    # List files again to find the final part file (which starts with "part-")
    files = dbutils.fs.ls(folder_path)
    for file in files:
        if file.name.startswith("part-"):
            source_path = file.path
            destination_path = folder_path + "/" + new_name
            dbutils.fs.mv(source_path, destination_path)
            print(f"Renamed {file.name} to {new_name}")

# Define the path for the Gold container
gold_folder = "dbfs:/mnt/gold/"

# Remove unwanted files and rename the fact table file
remove_and_rename_files(gold_folder + "fact_table.parquet", "fact_table.parquet")

# Remove unwanted files and rename the customer dimension file
remove_and_rename_files(gold_folder + "dim_customer.parquet", "dim_customer.parquet")

# Remove unwanted files and rename the product dimension file
remove_and_rename_files(gold_folder + "dim_product.parquet", "dim_product.parquet")

# Remove unwanted files and rename the store dimension file
remove_and_rename_files(gold_folder + "dim_store.parquet", "dim_store.parquet")

# Remove unwanted files and rename the inventory dimension file
remove_and_rename_files(gold_folder + "dim_inventory.parquet", "dim_inventory.parquet")

# Verify the files are renamed and the unwanted files are removed
dbutils.fs.ls(gold_folder)


Removed _SUCCESS
Removed _committed_1724314976863673345
Removed _started_1724314976863673345
Renamed part-00000-tid-1724314976863673345-a43f3337-dde7-40b2-af73-841d86e873a1-111-1-c000.snappy.parquet to fact_table.parquet
Removed _SUCCESS
Removed _committed_2324058674793548443
Removed _started_2324058674793548443
Renamed part-00000-tid-2324058674793548443-85ac99af-206d-4250-b506-1e89120ef453-112-1-c000.snappy.parquet to dim_customer.parquet
Removed _SUCCESS
Removed _committed_5726111440960110161
Removed _started_5726111440960110161
Renamed part-00000-tid-5726111440960110161-473aeada-fc41-4a3d-a127-6284946cec65-113-1-c000.snappy.parquet to dim_product.parquet
Removed _SUCCESS
Removed _committed_2547307835806829288
Removed _started_2547307835806829288
Renamed part-00000-tid-2547307835806829288-a4d49eae-30ce-41d5-ae35-64384d7f0fb0-114-1-c000.snappy.parquet to dim_store.parquet
Removed _SUCCESS
Removed _committed_8899661536288504088
Removed _started_8899661536288504088
Renamed part-00000-ti

[FileInfo(path='dbfs:/mnt/gold/dim_customer.parquet/', name='dim_customer.parquet/', size=0, modificationTime=1745835436000),
 FileInfo(path='dbfs:/mnt/gold/dim_inventory.parquet/', name='dim_inventory.parquet/', size=0, modificationTime=1745835437000),
 FileInfo(path='dbfs:/mnt/gold/dim_product.parquet/', name='dim_product.parquet/', size=0, modificationTime=1745835436000),
 FileInfo(path='dbfs:/mnt/gold/dim_store.parquet/', name='dim_store.parquet/', size=0, modificationTime=1745835437000),
 FileInfo(path='dbfs:/mnt/gold/fact_table.parquet/', name='fact_table.parquet/', size=0, modificationTime=1745835435000)]